In [7]:
import pandas as pd
pd.set_option('display.float_format', lambda x: '%.9f' % x)
from yahoofinancials import YahooFinancials
import datetime
from dateutil.relativedelta import relativedelta

In [47]:
 ##STEP 5:
#downloads daily ibovespa prices from investing.com and pushes it to the database
print('downloading ibovespa index prices from investing.com ...\n')
today = (datetime.date.today() + datetime.timedelta(1)).strftime('%Y-%m-%d')
ibov = pd.DataFrame(YahooFinancials('^BVSP').get_historical_price_data('2016-12-01', today, 'daily')['^BVSP']['prices'])
ibov = ibov.drop(columns=['date', 'close']).rename(columns={'formatted_date':'DT_COTACAO', 'adjclose':'FECHAMENTO', 'volume':'VOLUME'}).iloc[:,[5,0,1,2,3,4]]
ibov = ibov.drop(columns=['high','low','open'])
ibov['DT_COTACAO'] = pd.to_datetime(ibov['DT_COTACAO'])

# cria coluna MES_COMPTC (para auxiliar mais adiante)
ibov['MES_COTACAO']=ibov['DT_COTACAO'].apply(lambda x : x.replace(day=1))
ibov=ibov[['DT_COTACAO','FECHAMENTO','VOLUME','MES_COTACAO']]

#
#ibov.to_sql('tbl_ibovespa', con, index=False) 
#

downloading ibovespa index prices from investing.com ...



In [42]:
(datetime.date.today() + datetime.timedelta(0)).strftime('%Y-%m-%d')

'2021-06-24'

In [48]:
ultimo_pregao = ibov['DT_COTACAO'].max()
ultimo_pregao

Timestamp('2021-06-24 00:00:00')

<div class="alert-warning">    
    <h4><br>&nbsp; Última data de cada mês no dataframe <u>df</u>...<br>
    </h4>
</div>

In [49]:
#
# encontra a ultima data de cada mês
#
ibov_dt = ibov.groupby(['MES_COTACAO']).agg({'DT_COTACAO':'max'})
ibov_dt = ibov_dt.reset_index()
meses = ibov_dt['MES_COTACAO']
ibov_dt = ibov_dt.drop(['MES_COTACAO'], axis=1)
ibov_dt.rename(columns={'DT_COTACAO':'UltimoDiaMes'}, inplace=True)

In [50]:
ibov_dt

UltimoDiaMes
0    2016-12-29
1    2017-01-31
2    2017-02-24
3    2017-03-31
4    2017-04-28
5    2017-05-31
6    2017-06-30
7    2017-07-31
8    2017-08-31
9    2017-09-29
10   2017-10-31
11   2017-11-30
12   2017-12-29
13   2018-01-31
14   2018-02-28
15   2018-03-29
16   2018-04-30
17   2018-05-30
18   2018-06-29
19   2018-07-31
20   2018-08-31
21   2018-09-28
22   2018-10-31
23   2018-11-30
24   2018-12-28
25   2019-01-31
26   2019-02-28
27   2019-03-29
28   2019-04-30
29   2019-05-31
30   2019-06-28
31   2019-07-31
32   2019-08-30
33   2019-09-30
34   2019-10-31
35   2019-11-29
36   2019-12-30
37   2020-01-31
38   2020-02-28
39   2020-03-31
40   2020-04-30
41   2020-05-29
42   2020-06-30
43   2020-07-31
44   2020-08-31
45   2020-09-30
46   2020-10-30
47   2020-11-30
48   2020-12-30
49   2021-01-29
50   2021-02-26
51   2021-03-31
52   2021-04-30
53   2021-05-31
54   2021-06-24

In [51]:
meses

0    2016-12-01
1    2017-01-01
2    2017-02-01
3    2017-03-01
4    2017-04-01
5    2017-05-01
6    2017-06-01
7    2017-07-01
8    2017-08-01
9    2017-09-01
10   2017-10-01
11   2017-11-01
12   2017-12-01
13   2018-01-01
14   2018-02-01
15   2018-03-01
16   2018-04-01
17   2018-05-01
18   2018-06-01
19   2018-07-01
20   2018-08-01
21   2018-09-01
22   2018-10-01
23   2018-11-01
24   2018-12-01
25   2019-01-01
26   2019-02-01
27   2019-03-01
28   2019-04-01
29   2019-05-01
30   2019-06-01
31   2019-07-01
32   2019-08-01
33   2019-09-01
34   2019-10-01
35   2019-11-01
36   2019-12-01
37   2020-01-01
38   2020-02-01
39   2020-03-01
40   2020-04-01
41   2020-05-01
42   2020-06-01
43   2020-07-01
44   2020-08-01
45   2020-09-01
46   2020-10-01
47   2020-11-01
48   2020-12-01
49   2021-01-01
50   2021-02-01
51   2021-03-01
52   2021-04-01
53   2021-05-01
54   2021-06-01
Name: MES_COTACAO, dtype: datetime64[ns]

In [52]:
#
# exclui datas desnecessárias do dataframe
#
print('ibov contem:')
print(ibov.shape)
print('-'*75)
print('excluindo datas desnecessárias....')
ibov= ibov[ibov['DT_COTACAO'].isin(ibov_dt['UltimoDiaMes'])]
print('ibov contem:')
print(ibov.shape)
print('-'*75)


ibov contem:
(1135, 4)
---------------------------------------------------------------------------
excluindo datas desnecessárias....
ibov contem:
(55, 4)
---------------------------------------------------------------------------


In [53]:
ibov

DT_COTACAO  FECHAMENTO      VOLUME MES_COTACAO
20   2016-12-29    60227.00  2119500.00  2016-12-01
41   2017-01-31    64671.00  2737700.00  2017-01-01
59   2017-02-24    66662.00  3059900.00  2017-02-01
82   2017-03-31    64984.00  2614200.00  2017-03-01
100  2017-04-28    65403.00  2973700.00  2017-04-01
122  2017-05-31    62711.00  4535100.00  2017-05-01
144  2017-06-30    62900.00  2688200.00  2017-06-01
165  2017-07-31    65920.00  2572700.00  2017-07-01
188  2017-08-31    70835.00  4245100.00  2017-08-01
209  2017-09-29    74294.00  3126600.00  2017-09-01
231  2017-10-31    74308.00  3545700.00  2017-10-01
253  2017-11-30    71971.00  5348800.00  2017-11-01
274  2017-12-29    76402.00        0.00  2017-12-01
296  2018-01-31    84913.00  4233500.00  2018-01-01
314  2018-02-28    85481.00  5947100.00  2018-02-01
335  2018-03-29    85366.00  3150300.00  2018-03-01
356  2018-04-30    86115.00  2181000.00  2018-04-01
377  2018-05-30    76754.00  7442100.00  2018-05-01
398  2018-06-29    72763.00  3879400.00  2018-06-01
419  2018-07-31    79220.00  3354500.00  2018-07-01
442  2018-08-31    76678.00  4145600.00  2018-08-01
461  2018-09-28    79342.00  4061400.00  2018-09-01
483  2018-10-31    87424.00  5889800.00  2018-10-01
502  2018-11-30    89504.00  6736700.00  2018-11-01
520  2018-12-28    87887.00  3649100.00  2018-12-01
541  2019-01-31    97394.00  5976000.00  2019-01-01
561  2019-02-28    95584.00  5365700.00  2019-02-01
580  2019-03-29    95415.00  4674600.00  2019-03-01
601  2019-04-30    96353.00  4228600.00  2019-04-01
623  2019-05-31    97030.00  5089500.00  2019-05-01
642  2019-06-28   100967.00  4079900.00  2019-06-01
664  2019-07-31   101812.00  5072900.00  2019-07-01
686  2019-08-30   101135.00  6109600.00  2019-08-01
707  2019-09-30   104745.00  3895800.00  2019-09-01
730  2019-10-31   107220.00  5376000.00  2019-10-01
749  2019-11-29   108233.00  4186600.00  2019-11-01
768  2019-12-30   115964.00  3667900.00  2019-12-01
790  2020-01-31   113761.00  6219900.00  2020-01-01
808  2020-02-28   104172.00 11228400.00  2020-02-01
830  2020-03-31    73020.00 11141500.00  2020-03-01
850  2020-04-30    80506.00 11804600.00  2020-04-01
870  2020-05-29    87403.00 16550900.00  2020-05-01
891  2020-06-30    95056.00 10144500.00  2020-06-01
914  2020-07-31   102912.00 12929300.00  2020-07-01
935  2020-08-31    99369.00 12226100.00  2020-08-01
956  2020-09-30    94603.00  9454300.00  2020-09-01
977  2020-10-30    93952.00 10643200.00  2020-10-01
996  2020-11-30   108888.00 19300000.00  2020-11-01
1016 2020-12-30   119306.00  8235700.00  2020-12-01
1035 2021-01-29   116007.00 10965200.00  2021-01-01
1053 2021-02-26   110035.00 14618500.00  2021-02-01
1076 2021-03-31   116634.00 10659200.00  2021-03-01
1096 2021-04-30   118894.00 11093200.00  2021-04-01
1117 2021-05-31   126216.00  5946500.00  2021-05-01
1134 2021-06-24   129513.62        0.00  2021-06-01

In [75]:
##STEP 6:
#downloads daily selic returns (basic interest rate of the brazilian economy) 
#from the brazillian central bank and pushes it to the database
print('downloading selic rates from the Brazilian Central Bank website...\n')
# https://www.bcb.gov.br/htms/SELIC/SELICdiarios.asp?frame=1
selic = pd.read_json('http://api.bcb.gov.br/dados/serie/bcdata.sgs.{}/dados?formato=json'.format(11))
selic['data'] = pd.to_datetime(selic['data'], format = '%d/%m/%Y')
selic['valor'] = selic['valor']/100 
#calculates decimal rate from the percentual value
selic.rename(columns = {'data':'DT_COTACAO', 'valor':'TAXA'}, inplace = True)
selic=selic.style.format({'TAXA':'{:10.9f}'})

#selic.to_sql('tbl_selic', con , index=False)  

downloading selic rates from the Brazilian Central Bank website...



In [81]:
#c=selic
c.info()


AttributeError: 'Styler' object has no attribute 'info'

In [76]:
selic

In [79]:
selic.shape

AttributeError: 'Styler' object has no attribute 'shape'

In [6]:
#!pip install yahoofinancials